In [1]:
import pandas as pd
import numpy as np
import os
import matplotlib.pyplot as plt
from matplotlib import rcParams
from IPython.display import display
pd.options.display.max_columns = None

In [2]:
def test_dependency(df, col1, col2):
    '''From Brina Seidel's Lab 4 Notebook
    
       Tests whether there is total redundancy betwen col1 and col2
       by testing the number of unique combinations'''
    unique_1 = len(df[col1].unique())
    unique_2 = len(df[col2].unique())
    unique_combos = len(df[[col1, col2]].drop_duplicates())
    print("Unique values of {}: {}".format(col1, unique_1))
    print("Unique values of {}: {}".format(col2, unique_2))
    print("Unique combos of {} and {}: {}".format(col1, col2, unique_combos))
    return unique_combos == max(unique_1, unique_2)

In [4]:
init = pd.read_csv('Initiation.csv')
dispo = pd.read_csv('Dispositions.csv')
sent = pd.read_csv('Sentencing.csv')

/Users/AKR/HackLife/anaconda3/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3063: DtypeWarning: Columns (7,8,11) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)
/Users/AKR/HackLife/anaconda3/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3063: DtypeWarning: Columns (7,8,21) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [5]:
init.columns

Index(['CASE_ID', 'CASE_PARTICIPANT_ID', 'OFFENSE_CATEGORY', 'PRIMARY_CHARGE',
       'CHARGE_ID', 'CHARGE_VERSION_ID', 'CHARGE_OFFENSE_TITLE', 'CHAPTER',
       'ACT', 'SECTION', 'CLASS', 'AOIC', 'EVENT', 'EVENT_DATE',
       'AGE_AT_INCIDENT', 'GENDER', 'RACE', 'INCIDENT_BEGIN_DATE',
       'INCIDENT_END_DATE', 'ARREST_DATE', 'LAW_ENFORCEMENT_AGENCY', 'UNIT',
       'INCIDENT_CITY', 'RECEIVED_DATE', 'ARRAIGNMENT_DATE',
       'UPDATED_OFFENSE_CATEGORY', 'CHARGE_COUNT'],
      dtype='object')

In [10]:
dispo.columns

Index(['CASE_ID', 'CASE_PARTICIPANT_ID', 'OFFENSE_CATEGORY', 'PRIMARY_CHARGE',
       'CHARGE_ID', 'CHARGE_VERSION_ID', 'DISPOSITION_CHARGED_OFFENSE_TITLE',
       'DISPOSITION_CHARGED_CHAPTER', 'DISPOSITION_CHARGED_ACT',
       'DISPOSITION_CHARGED_SECTION', 'DISPOSITION_CHARGED_CLASS',
       'DISPOSITION_CHARGED_AOIC', 'DISPOSITION_DATE', 'CHARGE_DISPOSITION',
       'CHARGE_DISPOSITION_REASON', 'JUDGE', 'COURT_NAME', 'COURT_FACILITY',
       'AGE_AT_INCIDENT', 'GENDER', 'RACE', 'INCIDENT_BEGIN_DATE',
       'INCIDENT_END_DATE', 'ARREST_DATE', 'LAW_ENFORCEMENT_AGENCY', 'UNIT',
       'INCIDENT_CITY', 'RECEIVED_DATE', 'ARRAIGNMENT_DATE',
       'UPDATED_OFFENSE_CATEGORY', 'CHARGE_COUNT'],
      dtype='object')

In [20]:
sent.columns

Index(['CASE_ID', 'CASE_PARTICIPANT_ID', 'OFFENSE_CATEGORY', 'PRIMARY_CHARGE',
       'CHARGE_ID', 'CHARGE_VERSION_ID', 'DISPOSITION_CHARGED_OFFENSE_TITLE',
       'DISPOSITION_CHARGED_CHAPTER', 'DISPOSITION_CHARGED_ACT',
       'DISPOSITION_CHARGED_SECTION', 'DISPOSITION_CHARGED_CLASS',
       'DISPOSITION_CHARGED_AOIC', 'DISPOSITION_DATE', 'CHARGE_DISPOSITION',
       'CHARGE_DISPOSITION_REASON', 'SENTENCE_PHASE', 'SENTENCE_DATE',
       'SENTENCE_JUDGE', 'SENTENCE_TYPE', 'CURRENT_SENTENCE',
       'COMMITMENT_TYPE', 'COMMITMENT_TERM', 'COMMITMENT_UNIT', 'COURT_NAME',
       'COURT_FACILITY', 'LENGTH_OF_CASE_in_Days', 'AGE_AT_INCIDENT', 'GENDER',
       'RACE', 'INCIDENT_BEGIN_DATE', 'INCIDENT_END_DATE', 'ARREST_DATE',
       'LAW_ENFORCEMENT_AGENCY', 'UNIT', 'INCIDENT_CITY', 'RECEIVED_DATE',
       'ARRAIGNMENT_DATE', 'UPDATED_OFFENSE_CATEGORY', 'CHARGE_COUNT'],
      dtype='object')

## Indentifying Candidate Keys

In [8]:
test_dependency(init, 'CASE_PARTICIPANT_ID', 'CHARGE_ID')

Unique values of CASE_PARTICIPANT_ID: 334417
Unique values of CHARGE_ID: 848542
Unique combos of CASE_PARTICIPANT_ID and CHARGE_ID: 904719


False

In [9]:
len(init)

904719

In [13]:
test_dependency(dispo, 'CASE_PARTICIPANT_ID', 'CHARGE_ID')

Unique values of CASE_PARTICIPANT_ID: 312616
Unique values of CHARGE_ID: 779723
Unique combos of CASE_PARTICIPANT_ID and CHARGE_ID: 821723


False

In [14]:
len(dispo)

821723

In [21]:
test_dependency(sent, 'CASE_PARTICIPANT_ID', 'CHARGE_ID')

Unique values of CASE_PARTICIPANT_ID: 201181
Unique values of CHARGE_ID: 217597
Unique combos of CASE_PARTICIPANT_ID and CHARGE_ID: 227049


False

In [22]:
len(sent)

236124

#### We see that 'CASE_PARTICIPANT_ID' + 'CHARGE_ID' forms a candidate key in the Initiation and Dispositions datasets, but not in Sentencing. This indicates that each row in Initiation and Disposition represents a single charge against a person.

## Looking for Candidate Key in Sentencing Dataset

In [81]:
# Algorithm inspired by A Priori / Candidate Generation

'''
Use CP ID, Charge ID, Charge Version ID, and sentencing-related features
as potential building blocks for candidate key
'''

F = {1:[['CASE_PARTICIPANT_ID'], ['CHARGE_ID'], ['CHARGE_VERSION_ID'],
        ['SENTENCE_PHASE'], ['SENTENCE_DATE'], ['SENTENCE_JUDGE'], 
        ['SENTENCE_TYPE'], ['CURRENT_SENTENCE'],['COMMITMENT_TYPE'], 
        ['COMMITMENT_TERM'], ['COMMITMENT_UNIT'], ['COURT_NAME'],
        ['COURT_FACILITY'], ['LENGTH_OF_CASE_in_Days']]}

candidate_keys=[]

In [82]:
for k in range(1,len(F[1])):
    print('k='+str(k))
    F[k+1]=[]
    for group in F[k]:
        print('\t group: ', group)
        for col in F[1]:
            if col[0] not in group and group[-1]<col[0]:
                new_group = group.copy()+col
                if len(sent[new_group].drop_duplicates())==len(sent):
                    print('Candidate key: ', new_group)
                    candidate_keys.append(new_group)
                else:
                #search for further supersets if candidate key not identified
                    F[k+1].append(new_group)
                    print('\t\t new_group: ', new_group)

k=1
	 group:  ['CASE_PARTICIPANT_ID']
		 new_group:  ['CASE_PARTICIPANT_ID', 'CHARGE_ID']
		 new_group:  ['CASE_PARTICIPANT_ID', 'CHARGE_VERSION_ID']
		 new_group:  ['CASE_PARTICIPANT_ID', 'SENTENCE_PHASE']
		 new_group:  ['CASE_PARTICIPANT_ID', 'SENTENCE_DATE']
		 new_group:  ['CASE_PARTICIPANT_ID', 'SENTENCE_JUDGE']
		 new_group:  ['CASE_PARTICIPANT_ID', 'SENTENCE_TYPE']
		 new_group:  ['CASE_PARTICIPANT_ID', 'CURRENT_SENTENCE']
		 new_group:  ['CASE_PARTICIPANT_ID', 'COMMITMENT_TYPE']
		 new_group:  ['CASE_PARTICIPANT_ID', 'COMMITMENT_TERM']
		 new_group:  ['CASE_PARTICIPANT_ID', 'COMMITMENT_UNIT']
		 new_group:  ['CASE_PARTICIPANT_ID', 'COURT_NAME']
		 new_group:  ['CASE_PARTICIPANT_ID', 'COURT_FACILITY']
		 new_group:  ['CASE_PARTICIPANT_ID', 'LENGTH_OF_CASE_in_Days']
	 group:  ['CHARGE_ID']
		 new_group:  ['CHARGE_ID', 'CHARGE_VERSION_ID']
		 new_group:  ['CHARGE_ID', 'SENTENCE_PHASE']
		 new_group:  ['CHARGE_ID', 'SENTENCE_DATE']
		 new_group:  ['CHARGE_ID', 'SENTENCE_JUDGE']
		

		 new_group:  ['CASE_PARTICIPANT_ID', 'COMMITMENT_TYPE', 'SENTENCE_DATE']
		 new_group:  ['CASE_PARTICIPANT_ID', 'COMMITMENT_TYPE', 'SENTENCE_JUDGE']
		 new_group:  ['CASE_PARTICIPANT_ID', 'COMMITMENT_TYPE', 'SENTENCE_TYPE']
		 new_group:  ['CASE_PARTICIPANT_ID', 'COMMITMENT_TYPE', 'CURRENT_SENTENCE']
		 new_group:  ['CASE_PARTICIPANT_ID', 'COMMITMENT_TYPE', 'COMMITMENT_UNIT']
		 new_group:  ['CASE_PARTICIPANT_ID', 'COMMITMENT_TYPE', 'COURT_NAME']
		 new_group:  ['CASE_PARTICIPANT_ID', 'COMMITMENT_TYPE', 'COURT_FACILITY']
		 new_group:  ['CASE_PARTICIPANT_ID', 'COMMITMENT_TYPE', 'LENGTH_OF_CASE_in_Days']
	 group:  ['CASE_PARTICIPANT_ID', 'COMMITMENT_TERM']
		 new_group:  ['CASE_PARTICIPANT_ID', 'COMMITMENT_TERM', 'SENTENCE_PHASE']
		 new_group:  ['CASE_PARTICIPANT_ID', 'COMMITMENT_TERM', 'SENTENCE_DATE']
		 new_group:  ['CASE_PARTICIPANT_ID', 'COMMITMENT_TERM', 'SENTENCE_JUDGE']
		 new_group:  ['CASE_PARTICIPANT_ID', 'COMMITMENT_TERM', 'SENTENCE_TYPE']
		 new_group:  ['CASE_PARTICIPAN

		 new_group:  ['CHARGE_ID', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE']
		 new_group:  ['CHARGE_ID', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_JUDGE']
		 new_group:  ['CHARGE_ID', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_TYPE']
	 group:  ['CHARGE_VERSION_ID', 'SENTENCE_PHASE']
		 new_group:  ['CHARGE_VERSION_ID', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['CHARGE_VERSION_ID', 'SENTENCE_DATE']
		 new_group:  ['CHARGE_VERSION_ID', 'SENTENCE_DATE', 'SENTENCE_PHASE']
		 new_group:  ['CHARGE_VERSION_ID', 'SENTENCE_DATE', 'SENTENCE_JUDGE']
		 new_group:  ['CHARGE_VERSION_ID', 'SENTENCE_DATE', 'SENTENCE_TYPE']
	 group:  ['CHARGE_VERSION_ID', 'SENTENCE_JUDGE']
		 new_group:  ['CHARGE_VERSION_ID', 'SENTENCE_JUDGE', 'SENTENCE_PHASE']
		 new_group:  ['CHARGE_VERSION_ID', 'SENTENCE_JUDGE', 'SENTENCE_TYPE']
	 group:  ['CHARGE_VERSION_ID', 'SENTENCE_TYPE']
	 group:  ['CHARGE_VERSION_ID', 'CURRENT_SENTENCE']
		 new_group:  ['CHARGE_VERSION_ID', 'CURRENT_SENTENCE', 'SENTENCE_PHASE']
		 new_group:  ['CHARGE_VE

		 new_group:  ['COMMITMENT_TYPE', 'COURT_NAME', 'SENTENCE_JUDGE']
		 new_group:  ['COMMITMENT_TYPE', 'COURT_NAME', 'SENTENCE_TYPE']
		 new_group:  ['COMMITMENT_TYPE', 'COURT_NAME', 'CURRENT_SENTENCE']
		 new_group:  ['COMMITMENT_TYPE', 'COURT_NAME', 'LENGTH_OF_CASE_in_Days']
	 group:  ['COMMITMENT_TYPE', 'COURT_FACILITY']
		 new_group:  ['COMMITMENT_TYPE', 'COURT_FACILITY', 'SENTENCE_PHASE']
		 new_group:  ['COMMITMENT_TYPE', 'COURT_FACILITY', 'SENTENCE_DATE']
		 new_group:  ['COMMITMENT_TYPE', 'COURT_FACILITY', 'SENTENCE_JUDGE']
		 new_group:  ['COMMITMENT_TYPE', 'COURT_FACILITY', 'SENTENCE_TYPE']
		 new_group:  ['COMMITMENT_TYPE', 'COURT_FACILITY', 'CURRENT_SENTENCE']
		 new_group:  ['COMMITMENT_TYPE', 'COURT_FACILITY', 'COURT_NAME']
		 new_group:  ['COMMITMENT_TYPE', 'COURT_FACILITY', 'LENGTH_OF_CASE_in_Days']
	 group:  ['COMMITMENT_TYPE', 'LENGTH_OF_CASE_in_Days']
		 new_group:  ['COMMITMENT_TYPE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_PHASE']
		 new_group:  ['COMMITMENT_TYPE', 'LEN

		 new_group:  ['COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF_CASE_in_Days']
	 group:  ['COURT_NAME', 'LENGTH_OF_CASE_in_Days']
		 new_group:  ['COURT_NAME', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_PHASE']
		 new_group:  ['COURT_NAME', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE']
		 new_group:  ['COURT_NAME', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_JUDGE']
		 new_group:  ['COURT_NAME', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_TYPE']
	 group:  ['COURT_FACILITY', 'SENTENCE_PHASE']
		 new_group:  ['COURT_FACILITY', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['COURT_FACILITY', 'SENTENCE_DATE']
		 new_group:  ['COURT_FACILITY', 'SENTENCE_DATE', 'SENTENCE_PHASE']
		 new_group:  ['COURT_FACILITY', 'SENTENCE_DATE', 'SENTENCE_JUDGE']
		 new_group:  ['COURT_FACILITY', 'SENTENCE_DATE', 'SENTENCE_TYPE']
	 group:  ['COURT_FACILITY', 'SENTENCE_JUDGE']
		 new_group:  ['COURT_FACILITY', 'SENTENCE_JUDGE', 'SENTENCE_PHASE']
		 new_group:  ['COURT_FACILITY', 'SENTENCE_JUDGE', 'SENTENCE_TYPE']
	 group:  ['COURT_FACILIT

...

		 new_group:  ['CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TYPE', 'COMMITMENT_UNIT', 'COURT_FACILITY', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE', 'SENTENCE_JUDGE', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TYPE', 'COMMITMENT_UNIT', 'COURT_FACILITY', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE', 'SENTENCE_JUDGE', 'SENTENCE_TYPE']
	 group:  ['CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TYPE', 'COMMITMENT_UNIT', 'COURT_FACILITY', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_JUDGE', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TYPE', 'COMMITMENT_UNIT', 'COURT_FACILITY', 'COURT_NAME', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE', 'SENTENCE_JUDGE', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TYPE', 'COURT_FACILITY', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF

		 new_group:  ['CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TERM', 'COMMITMENT_TYPE', 'COURT_FACILITY', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE', 'SENTENCE_JUDGE', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TERM', 'COMMITMENT_TYPE', 'COURT_FACILITY', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE', 'SENTENCE_JUDGE', 'SENTENCE_TYPE']
	 group:  ['CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TERM', 'COMMITMENT_TYPE', 'COURT_FACILITY', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_JUDGE', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TERM', 'COMMITMENT_TYPE', 'COURT_FACILITY', 'COURT_NAME', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE', 'SENTENCE_JUDGE', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TERM', 'COMMITMENT_UNIT', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_O

		 new_group:  ['CASE_PARTICIPANT_ID', 'CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TYPE', 'COMMITMENT_UNIT', 'COURT_FACILITY', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE', 'SENTENCE_JUDGE', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['CASE_PARTICIPANT_ID', 'CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TYPE', 'COMMITMENT_UNIT', 'COURT_FACILITY', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE', 'SENTENCE_JUDGE', 'SENTENCE_TYPE']
	 group:  ['CASE_PARTICIPANT_ID', 'CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TYPE', 'COMMITMENT_UNIT', 'COURT_FACILITY', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_JUDGE', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['CASE_PARTICIPANT_ID', 'CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TYPE', 'COMMITMENT_UNIT', 'COURT_FACILITY', 'COURT_NAME', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE', 'SENTENCE_JUDGE', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['CASE_PARTICIPANT_ID', 

Candidate key:  ['CASE_PARTICIPANT_ID', 'CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TERM', 'COMMITMENT_TYPE', 'COURT_FACILITY', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE', 'SENTENCE_JUDGE', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['CASE_PARTICIPANT_ID', 'CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TERM', 'COMMITMENT_TYPE', 'COURT_FACILITY', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE', 'SENTENCE_JUDGE', 'SENTENCE_TYPE']
	 group:  ['CASE_PARTICIPANT_ID', 'CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TERM', 'COMMITMENT_TYPE', 'COURT_FACILITY', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_JUDGE', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['CASE_PARTICIPANT_ID', 'CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TERM', 'COMMITMENT_TYPE', 'COURT_FACILITY', 'COURT_NAME', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE', 'SENTENCE_JUDGE', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['CASE_PARTICIPANT_ID',

		 new_group:  ['CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TERM', 'COMMITMENT_TYPE', 'COMMITMENT_UNIT', 'COURT_FACILITY', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE', 'SENTENCE_JUDGE', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TERM', 'COMMITMENT_TYPE', 'COMMITMENT_UNIT', 'COURT_FACILITY', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE', 'SENTENCE_JUDGE', 'SENTENCE_TYPE']
	 group:  ['CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TERM', 'COMMITMENT_TYPE', 'COMMITMENT_UNIT', 'COURT_FACILITY', 'COURT_NAME', 'CURRENT_SENTENCE', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_JUDGE', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['CHARGE_ID', 'CHARGE_VERSION_ID', 'COMMITMENT_TERM', 'COMMITMENT_TYPE', 'COMMITMENT_UNIT', 'COURT_FACILITY', 'COURT_NAME', 'LENGTH_OF_CASE_in_Days', 'SENTENCE_DATE', 'SENTENCE_JUDGE', 'SENTENCE_PHASE', 'SENTENCE_TYPE']
	 group:  ['CHARGE_ID', 'CHARGE_VERSION_ID', 'COMM

In [91]:
F

{1: [['CASE_PARTICIPANT_ID'],
  ['CHARGE_ID'],
  ['CHARGE_VERSION_ID'],
  ['SENTENCE_PHASE'],
  ['SENTENCE_DATE'],
  ['SENTENCE_JUDGE'],
  ['SENTENCE_TYPE'],
  ['CURRENT_SENTENCE'],
  ['COMMITMENT_TYPE'],
  ['COMMITMENT_TERM'],
  ['COMMITMENT_UNIT'],
  ['COURT_NAME'],
  ['COURT_FACILITY'],
  ['LENGTH_OF_CASE_in_Days']],
 2: [['CASE_PARTICIPANT_ID', 'CHARGE_ID'],
  ['CASE_PARTICIPANT_ID', 'CHARGE_VERSION_ID'],
  ['CASE_PARTICIPANT_ID', 'SENTENCE_PHASE'],
  ['CASE_PARTICIPANT_ID', 'SENTENCE_DATE'],
  ['CASE_PARTICIPANT_ID', 'SENTENCE_JUDGE'],
  ['CASE_PARTICIPANT_ID', 'SENTENCE_TYPE'],
  ['CASE_PARTICIPANT_ID', 'CURRENT_SENTENCE'],
  ['CASE_PARTICIPANT_ID', 'COMMITMENT_TYPE'],
  ['CASE_PARTICIPANT_ID', 'COMMITMENT_TERM'],
  ['CASE_PARTICIPANT_ID', 'COMMITMENT_UNIT'],
  ['CASE_PARTICIPANT_ID', 'COURT_NAME'],
  ['CASE_PARTICIPANT_ID', 'COURT_FACILITY'],
  ['CASE_PARTICIPANT_ID', 'LENGTH_OF_CASE_in_Days'],
  ['CHARGE_ID', 'CHARGE_VERSION_ID'],
  ['CHARGE_ID', 'SENTENCE_PHASE'],
  ['CHARGE_I

In [92]:
# view all candidate keys
candidate_keys

[['CASE_PARTICIPANT_ID',
  'CHARGE_ID',
  'COMMITMENT_TERM',
  'COMMITMENT_TYPE',
  'CURRENT_SENTENCE',
  'SENTENCE_DATE',
  'SENTENCE_PHASE',
  'SENTENCE_TYPE'],
 ['CASE_PARTICIPANT_ID',
  'CHARGE_VERSION_ID',
  'COMMITMENT_TERM',
  'COMMITMENT_TYPE',
  'CURRENT_SENTENCE',
  'SENTENCE_DATE',
  'SENTENCE_PHASE',
  'SENTENCE_TYPE'],
 ['CASE_PARTICIPANT_ID',
  'CHARGE_ID',
  'CHARGE_VERSION_ID',
  'COMMITMENT_TERM',
  'COMMITMENT_TYPE',
  'CURRENT_SENTENCE',
  'SENTENCE_DATE',
  'SENTENCE_PHASE',
  'SENTENCE_TYPE'],
 ['CASE_PARTICIPANT_ID',
  'CHARGE_ID',
  'COMMITMENT_TERM',
  'COMMITMENT_TYPE',
  'CURRENT_SENTENCE',
  'SENTENCE_DATE',
  'SENTENCE_JUDGE',
  'SENTENCE_PHASE',
  'SENTENCE_TYPE'],
 ['CASE_PARTICIPANT_ID',
  'CHARGE_ID',
  'COMMITMENT_TERM',
  'COMMITMENT_TYPE',
  'CURRENT_SENTENCE',
  'LENGTH_OF_CASE_in_Days',
  'SENTENCE_DATE',
  'SENTENCE_PHASE',
  'SENTENCE_TYPE'],
 ['CASE_PARTICIPANT_ID',
  'CHARGE_ID',
  'COMMITMENT_TERM',
  'COMMITMENT_TYPE',
  'COMMITMENT_UNIT',
  '

In [93]:
# candidate keys of minimum length
[x for x in candidate_keys if len(x)==8]

[['CASE_PARTICIPANT_ID',
  'CHARGE_ID',
  'COMMITMENT_TERM',
  'COMMITMENT_TYPE',
  'CURRENT_SENTENCE',
  'SENTENCE_DATE',
  'SENTENCE_PHASE',
  'SENTENCE_TYPE'],
 ['CASE_PARTICIPANT_ID',
  'CHARGE_VERSION_ID',
  'COMMITMENT_TERM',
  'COMMITMENT_TYPE',
  'CURRENT_SENTENCE',
  'SENTENCE_DATE',
  'SENTENCE_PHASE',
  'SENTENCE_TYPE']]

In [86]:
# check for candidate keys that do not contain 'COMMITMENT_TERM'
[x for x in candidate_keys if 'COMMITMENT_TERM' not in x]

[]

#### Business rules that govern row-generation in the Sentencing dataset still not clear.

## Investigating Relationship between CHARGE_ID and CHARGE_VERSION_ID

In [17]:
test_dependency(dispo, 'CHARGE_ID', 'CHARGE_VERSION_ID')

Unique values of CHARGE_ID: 779723
Unique values of CHARGE_VERSION_ID: 784137
Unique combos of CHARGE_ID and CHARGE_VERSION_ID: 784137


True

In [19]:
test_dependency(init, 'CHARGE_ID', 'CHARGE_VERSION_ID')

Unique values of CHARGE_ID: 848542
Unique values of CHARGE_VERSION_ID: 848542
Unique combos of CHARGE_ID and CHARGE_VERSION_ID: 848542


True

In [18]:
test_dependency(sent, 'CHARGE_ID', 'CHARGE_VERSION_ID')

Unique values of CHARGE_ID: 217597
Unique values of CHARGE_VERSION_ID: 220786
Unique combos of CHARGE_ID and CHARGE_VERSION_ID: 220786


True

#### This shows that in all three datasets, each CHARGE_VERSION_ID corresponds to exactly 1 CHARGE_ID.

## Investigating Relationship between CASE_PARTICIPANT_ID and CASE_ID

In [11]:
test_dependency(init, 'CASE_PARTICIPANT_ID', 'CASE_ID')

Unique values of CASE_PARTICIPANT_ID: 334417
Unique values of CASE_ID: 310135
Unique combos of CASE_PARTICIPANT_ID and CASE_ID: 334417


True

In [94]:
test_dependency(dispo, 'CASE_PARTICIPANT_ID', 'CASE_ID')

Unique values of CASE_PARTICIPANT_ID: 312616
Unique values of CASE_ID: 291211
Unique combos of CASE_PARTICIPANT_ID and CASE_ID: 312616


True

In [95]:
test_dependency(sent, 'CASE_PARTICIPANT_ID', 'CASE_ID')

Unique values of CASE_PARTICIPANT_ID: 201181
Unique values of CASE_ID: 187239
Unique combos of CASE_PARTICIPANT_ID and CASE_ID: 201181


True

#### This confirms that in all 3 datasets, each CP ID corresponds to 1 person and 1 case.